In [1]:
from pyspark import SparkContext
from pyspark.sql import SparkSession
from pyspark import SparkConf
import pickle
from pyspark.sql.types import Row
from nltk.corpus import wordnet as wn
from textblob import TextBlob

conf = (SparkConf().setAppName("Assignment4"))
conf = (conf.set('spark.executor.memory', '8G').set('spark.driver.memory', '8G').
        set('spark.driver.maxResultSize', '8G'))
sc = SparkContext(conf = conf)
spark = SparkSession(sc)

#spark = SparkSession \
#    .builder \
#    .appName("Python Spark SQL basic example") \
#    .config("spark.some.config.option", "some-value") \
#    .getOrCreate()


5996996


In [2]:

df = spark.read.json("yelp_dataset/yelp_academic_dataset_review.json")
print(df.count())


5996996


In [3]:
# Load business_id that we want

las_vegas_business_ids = pickle.load(open("util_data/las_vegas_business_ids.pkl", "rb"))

business_to_cat = las_vegas_business_ids['business_to_category_mapping']
las_vegas_business_ids = set(las_vegas_business_ids['business_details'].keys())
#las_vegas_business_ids = set(["iCQpiavjjPzJ5_3gPD5Ebg"])
#print(len(las_vegas_business_ids))

#las_vegas_business_ids = set(["a","b"])

# Filter reviews that are made on las_vegas business

df = df[df['business_id'].isin(las_vegas_business_ids)]
print(df.count())
df.show(5)
#las_vegas_business_ids


1825333


+--------------------+----+----------+-----+--------------------+-----+--------------------+------+--------------------+
|         business_id|cool|      date|funny|           review_id|stars|                text|useful|             user_id|
+--------------------+----+----------+-----+--------------------+-----+--------------------+------+--------------------+
|iCQpiavjjPzJ5_3gP...|   0|2011-02-25|    0|x7mDIiDB3jEiPGPHO...|    2|The pizza was oka...|     0|msQe1u7Z_XuqjGoqh...|
|pomGBqfbxcqPv14c3...|   0|2012-11-13|    0|dDl8zu1vWPdKGihJr...|    5|I love this place...|     0|msQe1u7Z_XuqjGoqh...|
|jtQARsP6P-LbkyjbO...|   1|2014-10-23|    1|LZp4UX5zK3e-c5ZGS...|    1|Terrible. Dry cor...|     3|msQe1u7Z_XuqjGoqh...|
|elqbBhBfElMNSrjFq...|   0|2011-02-25|    0|Er4NBWCmCD4nM8_p1...|    2|Back in 2005-2007...|     2|msQe1u7Z_XuqjGoqh...|
|Ums3gaP2qM3W1XcA5...|   0|2014-09-05|    0|jsDu6QEJHbwP2Blom...|    5|Delicious healthy...|     0|msQe1u7Z_XuqjGoqh...|
+--------------------+----+-----

In [4]:
# Get all wordnet food names

food = wn.synset('food.n.02')
food_list = list(set([w.lower() for s in food.closure(lambda s:s.hyponyms()) for w in s.lemma_names()]))

In [5]:
# Extracting utilitiy matrix

def extract_food_in_text(text):
    ret_text = text.split()
    
    ret_text = [words.lower() for words in ret_text if words.lower() in food_list]
    
    return " ".join(ret_text)

def find_count(text):
    d = {}
    
    for word in text.split():
        if word in d:
            d[word] += 1
        else:
            d[word] = 1
    
    return d

def mix_dict(a,b):
    for key in a.keys():
        if key in b:
            b[key] += a[key]
        else:
            b[key] = a[key]
    
    return b

def map_to_category(food_counts, rating):
    if food_counts == {}:
        return None
    else:
        for food, count in food_counts.items():
            food_counts[food] = [(food_counts[food] * rating), 1]
        return food_counts

def extract_food_and_sentiment(review):
    global_dict = {}
    
    for sentence in review.split("."):
        sentiment = get_sentiment(sentence)
        food_det = find_count(extract_food_in_text(sentence))
        
        for food in food_det:
            if food in global_dict:
                global_dict[food] += sentiment
            else:
                global_dict[food] = sentiment
    
    return global_dict
        
def get_sentiment(sentence):
    sentence = TextBlob(sentence)
    return sentence.sentiment.polarity

def combine_dict(d1,d2):
    for key in d2.keys():
        if key in d1:
            d1[key] = [d1[key][0]+d2[key][0], d1[key][1]+d2[key][1]]
        else:
            d1[key] = [d2[key][0], d2[key][1]]
    
    return d1

def cal_average(d1):
    for key in d1:
        d1[key] = d1[key][0]/float(d1[key][1])
    
    return d1

'''
temp_rdd = df.rdd.map(lambda row: Row(row['business_id'], 
                            map_to_category(extract_food_and_sentiment(row['text']),
                                            row['stars'])
                                                                   ,row['user_id'], 
                                                                  row['review_id']))

food_review_df = spark.createDataFrame(temp_rdd).toDF(
    "business_id","stars","user_id","review_id")
food_review_df = food_review_df.where(food_review_df.stars.isNotNull())
food_review_df.show(5)
'''

temp_rdd = df.rdd.map(lambda row: Row(row['business_id'], 
                            map_to_category(extract_food_and_sentiment(row['text']),
                                            row['stars'])
                                                                   ,row['user_id'], 
                                                                  row['review_id']))
temp_rdd = temp_rdd.map(lambda row: (row[0],row[1])).filter(lambda row: row[1] != None)
temp_rdd = temp_rdd.reduceByKey(lambda x,y: combine_dict(x,y))
temp_rdd = temp_rdd.map(lambda row: (row[0], cal_average(row[1])))
business_to_food = temp_rdd.collect()

In [ ]:
import pickle
business_to_food = dict(business_to_food)
pickle.dump(business_to_food,open("util_data/business_to_food_mapping.pkl","wb"))
len(business_to_food)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
food_to_business = {}

for business in business_to_food:
    for food in business_to_food[business]:
        if food not in food_to_business:
            food_to_business[food] = {}
        
        food_to_business[food][business] = business_to_food[business][food]

food_to_business
pickle.dump(food_to_business, open("util_data/food_to_business_mapping.pkl","wb"))


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [4]:
# food_to_user_mapping
import pickle
food_to_user = {}

user_to_food = pickle.load(open("util_data/user_to_food_interest.pkl","rb"))

for user in user_to_food:
    for food in user_to_food[user]:
        if food not in food_to_user:
            food_to_user[food] = {}
        
        food_to_user[food][user] = user_to_food[user][food]

pickle.dump(food_to_user, open("util_data/food_to_user_mapping.pkl","wb"))

print(list(food_to_user.items())[:5])

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
# business to food mapping

food_review_df.select(['business_id','stars']).show(5)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
def user_food_rating(rows):
    rows = list(rows)
    ret_list = []
    
    for each_row in rows:
        user = each_row[2]
        stars = each_row[1]
        
        for food, rating in stars.items():
            ret_list.append((user, food, rating))
    
    return ret_list

user_to_food = food_review_df.rdd.mapPartitions(lambda rows: user_food_rating(rows))
user_to_food.take(5)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [8]:
user_to_food_list = user_to_food.collect()

638


In [10]:
pickle.dump(user_to_food_list,open(
    "util_data/user_to_food_rating_list_with_duplicates.pkl","wb+"))

638


In [4]:
import pickle

user_to_food_list = pickle.load(open(
    "util_data/user_to_food_rating_list_with_duplicates.pkl","rb"))
user_rating_for_food = {}

for user, food, rating in user_to_food_list:
    if user in user_rating_for_food:
        if food in user_rating_for_food[user]:
            user_rating_for_food[user][food] = \
    [user_rating_for_food[user][food][0]+rating,user_rating_for_food[user][food][1]+1]
        else:
            user_rating_for_food[user][food] = [rating, 1]
    else:
        user_rating_for_food[user] = {}
        user_rating_for_food[user][food] = [rating, 1]


In [5]:
for user in user_rating_for_food.keys():
    for food in user_rating_for_food[user].keys():
        user_rating_for_food[user][food] = user_rating_for_food[user][food][0] / float(user_rating_for_food[user][food][1])

with open("util_data/user_to_food_interest.txt","w+") as data_file:
    for user in user_rating_for_food.keys():
        for food in user_rating_for_food[user].keys():
            data_file.write(str(user)+","+str(food)+","+
                            str( user_rating_for_food[user][food])+"\n")

pickle.dump(user_rating_for_food,open("util_data/user_to_food_interest.pkl","wb"))

In [ ]:
# Create csv for each user vector to check sparsity
choosen_food = set()

for user in user_rating_for_food.keys():
    for food in user_rating_for_food[user].keys():
        choosen_food.add(food)

choosen_food = list(choosen_food)
print(len(choosen_food))
choosen_food = [(food, index) for index,food in enumerate(choosen_food)]
labels = [food[0] for food in sorted(choosen_food)]

choosen_food = dict(choosen_food)

with open("util_data/user_food_profile.csv","w+") as user_profile_file:
    user_profile_file.write("User,"+(",".join(labels))+"\n")
    
    for user in user_rating_for_food.keys():
        vector = [0] * len(choosen_food)
        for food in user_rating_for_food[user].keys():
            vector[choosen_food[food]] = user_rating_for_food[user][food]
        vector = [str(i) for i in vector]
        user_profile_file.write(str(user)+","+(",".join(vector))+"\n")


317240

In [1]:
user_profile_csv = open("util_data/user_food_profile.csv","r")
user_profile_csv = list(user_profile_csv)
user_profile_csv = user_profile_csv[1:]
user_profile = dict([(line.split(",")[0],
        [float(val) for val in line.split(",")[1:]]) for line in user_profile_csv])
len(user_profile)

317240

In [3]:
# cosine similarity
from sklearn.metrics.pairwise import cosine_similarity
users = list(user_profile.keys())

def get_similar_users(user):
    sim = [(user, user_profile[user]) for user in users]
    
    
    
    user_similarity = {}
    print("start")
    
    for user2_index in range(len(users)):
        print(user2_index,end="\r")
        if users[user2_index] == user:
            continue
        else:
            user_similarity[users[user2_index]] = cosine_similarity([user_profile[user]],[ 
                    user_profile[users[user2_index]]])
    return user_similarity

get_similar_users(users[0])

start
278

470

2053

2340

2576

...

314947

315724

316376

317214

{'0AIj432MvowwghnpurtP-Q': array([[0.]]),
 'Yy_iGXxLpL6tYDQoE-6XVg': array([[0.19725896]]),
 'dQzQ4bN0Rnb8M-0LqTl3-g': array([[0.24995327]]),
 'EfOhaQ-J5s9t2EmH0uBELw': array([[0.13375284]]),
 'FHwl6kaKdD5-KAnfVb_pKQ': array([[-0.04626677]]),
 'KA3YwBSc1oqe7SzHErshJA': array([[0.]]),
 'Rr4nRgrl3JVJPdDSz4__PA': array([[-0.11466553]]),
 'fo4mpUqgXL2mJqALc9AvbA': array([[-0.08448714]]),
 'AuIK5tF2GjO7SftHawTLKw': array([[0.19222124]]),
 'oZOBAtPYVUq724Wywoh5kg': array([[0.51219439]]),
 'TVvTtXwPXsvrg2KJGoOUTg': array([[0.27721136]]),
 'JIkVfsVYb7-26O3BxlyHAQ': array([[0.]]),
 'oY6vb4d0bMNf-b1H2w29iQ': array([[0.]]),
 'juE5LohVTruYea2SHV2HYA': array([[0.]]),
 'IqZ4tKOTEwvE8RBXKpyn6w': array([[0.]]),
 'wcKvC0jov-kAHg-GIvWJqg': array([[0.]]),
 'D1_nrBr4dOrs7M82OaBRwQ': array([[0.06085307]]),
 'nsrRDfgo4yMnb5EJEOlRjw': array([[0.]]),
 'qr9hmaIxq1z9ycgT28PpRw': array([[0.04832906]]),
 '1ryvfb9F6hYoCZZZaqeCOA': array([[0.18867678]]),
 'P_81hAwNnAzrITeTaKO8ZQ': array([[0.06543109]]),
 '5qz4ICJWJ

In [ ]:
# Lowest possible food names needed

def merge_dict(x,y):
    for k in y.keys():
        if k in x:
            x[k] = x[k].union(y[k])
        else:
            x[k] = y[k]
    
    return x
        

def food_to_cat(stars):
    glob_d = {}
    
    for each in stars:
        for food, cat in each[1].items():
            if food in glob_d:
                glob_d[food] = glob_d[food].union(set(cat))
            else:
                glob_d[food] = set(cat)
    
    glob_d = [(a,list(b)) for a,b in glob_d.items()]
    
    return glob_d

#word_to_reviews = food_review_df.rdd.map(lambda row: (dict([(food,set([row['review_id']]))
#                for food in list(row['stars'].keys())]))).reduce(lambda x,y: 
#                                                            x.update(y)).collect()

#word_to_reviews

#food_to_rev_map = food_review_df.rdd.map(lambda row: (dict([(food, set([row['review_id']]))
#                    for food in list(row['stars'].keys())]))).collect()

#.reduce(lambda x,y:merge_dict(x,y))


list_food = food_review_df.rdd.mapPartitions(lambda row: food_to_cat(row))
list_food.take(1)


start
278

470

2053

2340

2576

...

314947

315724

316376

317214

{'0AIj432MvowwghnpurtP-Q': array([[0.]]),
 'Yy_iGXxLpL6tYDQoE-6XVg': array([[0.19725896]]),
 'dQzQ4bN0Rnb8M-0LqTl3-g': array([[0.24995327]]),
 'EfOhaQ-J5s9t2EmH0uBELw': array([[0.13375284]]),
 'FHwl6kaKdD5-KAnfVb_pKQ': array([[-0.04626677]]),
 'KA3YwBSc1oqe7SzHErshJA': array([[0.]]),
 'Rr4nRgrl3JVJPdDSz4__PA': array([[-0.11466553]]),
 'fo4mpUqgXL2mJqALc9AvbA': array([[-0.08448714]]),
 'AuIK5tF2GjO7SftHawTLKw': array([[0.19222124]]),
 'oZOBAtPYVUq724Wywoh5kg': array([[0.51219439]]),
 'TVvTtXwPXsvrg2KJGoOUTg': array([[0.27721136]]),
 'JIkVfsVYb7-26O3BxlyHAQ': array([[0.]]),
 'oY6vb4d0bMNf-b1H2w29iQ': array([[0.]]),
 'juE5LohVTruYea2SHV2HYA': array([[0.]]),
 'IqZ4tKOTEwvE8RBXKpyn6w': array([[0.]]),
 'wcKvC0jov-kAHg-GIvWJqg': array([[0.]]),
 'D1_nrBr4dOrs7M82OaBRwQ': array([[0.06085307]]),
 'nsrRDfgo4yMnb5EJEOlRjw': array([[0.]]),
 'qr9hmaIxq1z9ycgT28PpRw': array([[0.04832906]]),
 '1ryvfb9F6hYoCZZZaqeCOA': array([[0.18867678]]),
 'P_81hAwNnAzrITeTaKO8ZQ': array([[0.06543109]]),
 '5qz4ICJWJ

In [18]:
list_food = list_food.collect()
pickle.dump(list_food, open("util_data/food_to_cat_intermediate.pkl","wb"))

In [22]:
type(list_food)

food_to_cat_map = {}

for food, cat in list_food:
    if food.lower() in food_to_cat_map:
        food_to_cat_map[food.lower()] = food_to_cat_map[food.lower()].union(set(cat))
    else:
        food_to_cat_map[food.lower()] = set(cat)

pickle.dump(food_to_cat_map, open("util_data/food_to_cat.pkl","wb"))


In [6]:
import pickle

food_to_cat_map = pickle.load(open("util_data/food_to_cat.pkl","rb"))

choosen_category = open("manually_choosen_categories.txt","r")
choosen_category = list(choosen_category)
choosen_category = [cat.strip().split("=")[0] for cat in choosen_category]
choosen_category = [cat.lower() for cat in choosen_category]
choosen_category = set(choosen_category)
choosen_category = dict([(food, index) for index,food in enumerate(choosen_category)])
choosen_category["generic"] = max(choosen_category.values())+1

with open("util_data/food_mappings.csv","w+") as mapping_file:
    temp = choosen_category.items()
    temp = sorted(temp, key=lambda k: k[1])
    temp = [k[0] for k in temp]
    mapping_file.write(","+(",".join(temp)+"\n"))
    for food, cat in food_to_cat_map.items():
        vector = [0] * len(choosen_category)
        for c in cat:
            vector[choosen_category[c]] = "FILL"
        vector = [str(i) for i in vector]
        mapping_file.write(str(food)+","+",".join(vector)+"\n")

In [23]:
# get frequent food from the extracted food words from review

z = df.rdd.map(lambda row: find_count(extract_food_in_text(row['text'])))
z = z.reduce(lambda x,y: mix_dict(x,y))

# lower cased food items

food = {}

for food_val in z.keys():
    if food_val.lower() in food:
        food[food_val.lower()].append(food_val)
    else:
        food[food_val.lower()] = [food_val]

for food_val in food.keys():
    count = 0
    
    for similar_names in food[food_val]:
        count += z[similar_names]
    
    food[food_val] = count

food_names = set(food.keys())
food_frequency = food
list(food_frequency.items())[:5]


In [34]:
# Store the frequency of different food used

pickle.dump(food_frequency, open("util_data/food_frequency_in_review.pkl", "wb"))


with open("util_data/food_frequency.txt","w+") as food_file:
    for food, count in sorted(list(food_frequency.items()), key=lambda x:x[1], reverse=True):
        food_file.write(str(food)+":"+str(count)+"\n")